![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Modelowanie języka</h1>
<h2> 7. <i>Zanurzenia słów</i>  [wykład]</h2> 
<h3> Filip Graliński (2022)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)



## Zanurzenia słów



W praktyce stosowalność słowosieci okazała się zaskakująco
ograniczona. Większy przełom w przetwarzaniu języka naturalnego przyniosły
wielowymiarowe reprezentacje słów, inaczej: zanurzenia słów.



### „Wymiary” słów



Moglibyśmy zanurzyć (ang. *embed*) w wielowymiarowej przestrzeni, tzn. zdefiniować odwzorowanie
$E \colon V \rightarrow \mathcal{R}^m$ dla pewnego $m$ i określić taki sposób estymowania
prawdopodobieństw $P(u|v)$, by dla par $E(v)$ i $E(v')$ oraz $E(u)$ i $E(u')$ znajdujących się w pobliżu
(według jakiejś metryki odległości, na przykład zwykłej odległości euklidesowej):

$$P(u|v) \approx P(u'|v').$$

$E(u)$ nazywamy zanurzeniem (embeddingiem) słowa.



#### Wymiary określone z góry?



Można by sobie wyobrazić, że $m$ wymiarów mogłoby być z góry
określonych przez lingwistę. Wymiary te byłyby związane z typowymi
„osiami” rozpatrywanymi w językoznawstwie, na przykład:

-   czy słowo jest wulgarne, pospolite, potoczne, neutralne czy książkowe?
-   czy słowo jest archaiczne, wychodzące z użycia czy jest neologizmem?
-   czy słowo dotyczy kobiet, czy mężczyzn (w sensie rodzaju gramatycznego i/lub
    socjolingwistycznym)?
-   czy słowo jest w liczbie pojedynczej czy mnogiej?
-   czy słowo jest rzeczownikiem czy czasownikiem?
-   czy słowo jest rdzennym słowem czy zapożyczeniem?
-   czy słowo jest nazwą czy słowem pospolitym?
-   czy słowo opisuje konkretną rzecz czy pojęcie abstrakcyjne?
-   …

W praktyce okazało się jednak, że lepiej, żeby komputer uczył się sam
możliwych wymiarów — z góry określamy tylko $m$ (liczbę wymiarów).



### Bigramowy model języka oparty na zanurzeniach



Zbudujemy teraz najprostszy model język oparty na zanurzeniach. Będzie to właściwie najprostszy
**neuronowy model języka**, jako że zbudowany model można traktować jako prostą sieć neuronową.



#### Słownik



W typowym neuronowym modelu języka rozmiar słownika musi być z góry
ograniczony. Zazwyczaj jest to liczba rzędu kilkudziesięciu wyrazów —
po prostu będziemy rozpatrywać $|V|$ najczęstszych wyrazów, pozostałe zamienimy
na specjalny token `<unk>` reprezentujący nieznany (*unknown*) wyraz.

Aby utworzyć taki słownik użyjemy gotowej klasy `Vocab` z pakietu torchtext:



In [2]:
from itertools import islice
import regex as re
import sys
from torchtext.vocab import build_vocab_from_iterator


def get_words_from_line(line):
  line = line.rstrip()
  yield '<s>'
  for m in re.finditer(r'[\p{L}0-9\*]+|\p{P}+', line):
     yield m.group(0).lower()
  yield '</s>'


def get_word_lines_from_file(file_name):
  with open(file_name, 'r') as fh:
    for line in fh:
       yield get_words_from_line(line)

vocab_size = 20000

vocab = build_vocab_from_iterator(
    get_word_lines_from_file('opensubtitlesA.pl.txt'),
    max_tokens = vocab_size,
    specials = ['<unk>'])

vocab['jest']

/media/kuba/ssdsam/anaconda3/envs/lmzajecia/lib/python3.10/site-packages/torch/_masked/__init__.py:223: UserWarning: Failed to initialize NumPy: No module named 'numpy' (Triggered internally at  /opt/conda/conda-bld/pytorch_1646755897462/work/torch/csrc/utils/tensor_numpy.cpp:68.)
  example_input = torch.tensor([[-3, -2, -1], [0, 1, 2]])


16

In [3]:
vocab.lookup_tokens([0, 1, 2, 10, 12345])

['<unk>', '</s>', '<s>', 'w', 'policyjny']

#### Definicja sieci



Naszą prostą sieć neuronową zaimplementujemy używając frameworku PyTorch.



In [4]:
from torch import nn
import torch

embed_size = 100

class SimpleBigramNeuralLanguageModel(nn.Module):
  def __init__(self, vocabulary_size, embedding_size):
      super(SimpleBigramNeuralLanguageModel, self).__init__()
      self.model = nn.Sequential(
          nn.Embedding(vocabulary_size, embedding_size),
          nn.Linear(embedding_size, vocabulary_size),
          nn.Softmax()
      )

  def forward(self, x):
      return self.model(x)

model = SimpleBigramNeuralLanguageModel(vocab_size, embed_size)

vocab.set_default_index(vocab['<unk>'])
ixs = torch.tensor(vocab.forward(['pies']))
out[0][vocab['jest']]

NameError: name 'out' is not defined

Teraz wyuczmy model. Wpierw tylko potasujmy nasz plik:

    shuf < opensubtitlesA.pl.txt > opensubtitlesA.pl.shuf.txt



In [6]:
!shuf < opensubtitlesA.pl.txt > opensubtitlesA.pl.shuf.txt

In [7]:
from torch.utils.data import IterableDataset
import itertools

def look_ahead_iterator(gen):
   prev = None
   for item in gen:
      if prev is not None:
         yield (prev, item)
      prev = item

class Bigrams(IterableDataset):
  def __init__(self, text_file, vocabulary_size):
      self.vocab = build_vocab_from_iterator(
         get_word_lines_from_file(text_file),
         max_tokens = vocabulary_size,
         specials = ['<unk>'])
      self.vocab.set_default_index(self.vocab['<unk>'])
      self.vocabulary_size = vocabulary_size
      self.text_file = text_file

  def __iter__(self):
     return look_ahead_iterator(
         (self.vocab[t] for t in itertools.chain.from_iterable(get_word_lines_from_file(self.text_file))))

train_dataset = Bigrams('opensubtitlesA.pl.shuf.txt', vocab_size)

In [8]:
from torch.utils.data import DataLoader

next(iter(train_dataset))

(2, 72)

In [9]:
from torch.utils.data import DataLoader

next(iter(DataLoader(train_dataset, batch_size=5)))

[tensor([  2,  72, 615,  11,  92]), tensor([ 72, 615,  11,  92,   4])]

In [13]:
    device = 'cuda'
    model = SimpleBigramNeuralLanguageModel(vocab_size, embed_size).to(device)
    data = DataLoader(train_dataset, batch_size=5000)
    optimizer = torch.optim.Adam(model.parameters())
    criterion = torch.nn.NLLLoss()
    
    model.train()
    step = 0
    for x, y in data:
       x = x.to(device)
       y = y.to(device)
       optimizer.zero_grad()
       ypredicted = model(x)
       loss = criterion(torch.log(ypredicted), y)
       if step % 100 == 0:
          print(step, loss)
       step += 1
       loss.backward()
       optimizer.step()
    
    torch.save(model.state_dict(), 'model1.bin')

#Policzmy najbardziej prawdopodobne kontynuację dla zadanego słowa:



/media/kuba/ssdsam/anaconda3/envs/lmzajecia/lib/python3.10/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


0 tensor(10.2158, device='cuda:0', grad_fn=<NllLossBackward0>)
100 tensor(6.9743, device='cuda:0', grad_fn=<NllLossBackward0>)
200 tensor(6.2186, device='cuda:0', grad_fn=<NllLossBackward0>)
300 tensor(5.6430, device='cuda:0', grad_fn=<NllLossBackward0>)
400 tensor(5.3539, device='cuda:0', grad_fn=<NllLossBackward0>)
500 tensor(5.0689, device='cuda:0', grad_fn=<NllLossBackward0>)
600 tensor(4.9418, device='cuda:0', grad_fn=<NllLossBackward0>)
700 tensor(4.8142, device='cuda:0', grad_fn=<NllLossBackward0>)
800 tensor(4.6436, device='cuda:0', grad_fn=<NllLossBackward0>)
900 tensor(4.6770, device='cuda:0', grad_fn=<NllLossBackward0>)
1000 tensor(4.6069, device='cuda:0', grad_fn=<NllLossBackward0>)
1100 tensor(4.5514, device='cuda:0', grad_fn=<NllLossBackward0>)
1200 tensor(4.5288, device='cuda:0', grad_fn=<NllLossBackward0>)
1300 tensor(4.4578, device='cuda:0', grad_fn=<NllLossBackward0>)
1400 tensor(4.5290, device='cuda:0', grad_fn=<NllLossBackward0>)
1500 tensor(4.5229, device='cuda:0',

12600 tensor(4.1542, device='cuda:0', grad_fn=<NllLossBackward0>)
12700 tensor(4.1810, device='cuda:0', grad_fn=<NllLossBackward0>)
12800 tensor(4.1948, device='cuda:0', grad_fn=<NllLossBackward0>)
12900 tensor(4.1085, device='cuda:0', grad_fn=<NllLossBackward0>)
13000 tensor(4.1283, device='cuda:0', grad_fn=<NllLossBackward0>)
13100 tensor(4.1548, device='cuda:0', grad_fn=<NllLossBackward0>)
13200 tensor(4.1015, device='cuda:0', grad_fn=<NllLossBackward0>)
13300 tensor(4.1342, device='cuda:0', grad_fn=<NllLossBackward0>)
13400 tensor(4.0724, device='cuda:0', grad_fn=<NllLossBackward0>)
13500 tensor(4.1006, device='cuda:0', grad_fn=<NllLossBackward0>)
13600 tensor(4.0998, device='cuda:0', grad_fn=<NllLossBackward0>)
13700 tensor(4.1021, device='cuda:0', grad_fn=<NllLossBackward0>)
13800 tensor(4.1175, device='cuda:0', grad_fn=<NllLossBackward0>)
13900 tensor(4.1017, device='cuda:0', grad_fn=<NllLossBackward0>)
14000 tensor(4.1877, device='cuda:0', grad_fn=<NllLossBackward0>)
14100 tens

25100 tensor(4.0505, device='cuda:0', grad_fn=<NllLossBackward0>)
25200 tensor(4.1542, device='cuda:0', grad_fn=<NllLossBackward0>)
25300 tensor(4.0740, device='cuda:0', grad_fn=<NllLossBackward0>)
25400 tensor(4.0893, device='cuda:0', grad_fn=<NllLossBackward0>)
25500 tensor(4.0370, device='cuda:0', grad_fn=<NllLossBackward0>)
25600 tensor(4.1480, device='cuda:0', grad_fn=<NllLossBackward0>)
25700 tensor(4.1070, device='cuda:0', grad_fn=<NllLossBackward0>)
25800 tensor(4.0381, device='cuda:0', grad_fn=<NllLossBackward0>)
25900 tensor(4.0800, device='cuda:0', grad_fn=<NllLossBackward0>)
26000 tensor(4.0842, device='cuda:0', grad_fn=<NllLossBackward0>)
26100 tensor(4.1127, device='cuda:0', grad_fn=<NllLossBackward0>)
26200 tensor(4.1184, device='cuda:0', grad_fn=<NllLossBackward0>)
26300 tensor(4.0885, device='cuda:0', grad_fn=<NllLossBackward0>)
26400 tensor(4.1423, device='cuda:0', grad_fn=<NllLossBackward0>)
26500 tensor(4.1359, device='cuda:0', grad_fn=<NllLossBackward0>)
26600 tens

In [14]:
model

SimpleBigramNeuralLanguageModel(
  (model): Sequential(
    (0): Embedding(20000, 100)
    (1): Linear(in_features=100, out_features=20000, bias=True)
    (2): Softmax(dim=None)
  )
)

In [15]:
device = 'cuda'
model = SimpleBigramNeuralLanguageModel(vocab_size, embed_size).to(device)
model.load_state_dict(torch.load('model1.bin'))
model.eval()

ixs = torch.tensor(vocab.forward(['dla'])).to(device)

out = model(ixs)
top = torch.topk(out[0], 10)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[('mnie', 26, 0.16004179418087006),
 ('ciebie', 73, 0.13592898845672607),
 ('<unk>', 0, 0.12769868969917297),
 ('nas', 83, 0.04033529385924339),
 ('niego', 172, 0.033195145428180695),
 ('niej', 247, 0.021507620811462402),
 ('was', 162, 0.017743170261383057),
 ('siebie', 181, 0.01618184894323349),
 ('nich', 222, 0.01589815877377987),
 ('pana', 156, 0.014923062175512314)]

Teraz zbadajmy najbardziej podobne zanurzenia dla zadanego słowa:



In [16]:
vocab = train_dataset.vocab
ixs = torch.tensor(vocab.forward(['kłopot'])).to(device)

out = model(ixs)
top = torch.topk(out[0], 10)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[('.', 3, 0.3327740728855133),
 ('z', 14, 0.191472589969635),
 (',', 4, 0.18250100314617157),
 ('w', 10, 0.06395534425973892),
 ('?', 6, 0.059775471687316895),
 ('i', 11, 0.019332991912961006),
 ('ze', 60, 0.016418060287833214),
 ('<unk>', 0, 0.014098692685365677),
 ('na', 12, 0.01183203887194395),
 ('...', 15, 0.010537521913647652)]

In [17]:
cos = nn.CosineSimilarity(dim=1, eps=1e-6)

embeddings = model.model[0].weight

vec = embeddings[vocab['poszedł']]

similarities = cos(vec, embeddings)

top = torch.topk(similarities, 10)

top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[('poszedł', 1088, 1.0),
 ('wsiąść', 9766, 0.46510031819343567),
 ('pojedzie', 6485, 0.4598822593688965),
 ('wyjeżdża', 6459, 0.4378735423088074),
 ('szedłem', 8969, 0.4232063889503479),
 ('zadzwoniłem', 4889, 0.41752171516418457),
 ('dotrzemy', 6098, 0.40929487347602844),
 ('spóźnić', 9923, 0.4015277922153473),
 ('pójdę', 635, 0.3992091119289398),
 ('wrócimy', 2070, 0.39785560965538025)]

#### Zapis przy użyciu wzoru matematycznego



Powyżej zaprogramowaną sieć neuronową można opisać następującym wzorem:

$$\vec{y} = \operatorname{softmax}(CE(w_{i-1}),$$

gdzie:

-   $w_{i-1}$ to pierwszy wyraz w bigramie (poprzedzający wyraz),
-   $E(w)$ to zanurzenie (embedding) wyrazy $w$ — wektor o rozmiarze $m$,
-   $C$ to macierz o rozmiarze $|V| \times m$, która rzutuje wektor zanurzenia w wektor o rozmiarze słownika,
-   $\vec{y}$ to wyjściowy wektor prawdopodobieństw o rozmiarze $|V|$.



##### Hiperparametry



Zauważmy, że nasz model ma dwa hiperparametry:

-   $m$ — rozmiar zanurzenia,
-   $|V|$ — rozmiar słownika, jeśli zakładamy, że możemy sterować
    rozmiarem słownika (np. przez obcinanie słownika do zadanej liczby
    najczęstszych wyrazów i zamiany pozostałych na specjalny token, powiedzmy, `<UNK>`.

Oczywiście możemy próbować manipulować wartościami $m$ i $|V|$ w celu
polepszenia wyników naszego modelu.

**Pytanie**: dlaczego nie ma sensu wartość $m \approx |V|$ ? dlaczego nie ma sensu wartość $m = 1$?



#### Diagram sieci



Jako że mnożenie przez macierz ($C$) oznacza po prostu zastosowanie
warstwy liniowej, naszą sieć możemy interpretować jako jednowarstwową
sieć neuronową, co można zilustrować za pomocą następującego diagramu:

![img](./07_Zanurzenia_slow/bigram1.drawio.png "Diagram prostego bigramowego neuronowego modelu języka")



#### Zanurzenie jako mnożenie przez macierz



Uzyskanie zanurzenia ($E(w)$) zazwyczaj realizowane jest na zasadzie
odpytania (<sub>look</sub>-up\_). Co ciekawe, zanurzenie można intepretować jako
mnożenie przez macierz zanurzeń (embeddingów) $E$ o rozmiarze $m \times |V|$ — jeśli słowo będziemy na wejściu kodowali przy użyciu
wektora z gorącą jedynką (<sub>one</sub>-hot encoding\_), tzn. słowo $w$ zostanie
podane na wejściu jako wektor $\vec{1_V}(w) = [0,\ldots,0,1,0\ldots,0]$ o rozmiarze $|V|$
złożony z samych zer z wyjątkiem jedynki na pozycji odpowiadającej indeksowi wyrazu $w$ w słowniku $V$.

Wówczas wzór przyjmie postać:

$$\vec{y} = \operatorname{softmax}(CE\vec{1_V}(w_{i-1})),$$

gdzie $E$ będzie tym razem macierzą $m \times |V|$.

**Pytanie**: czy $\vec{1_V}(w)$ intepretujemy jako wektor wierszowy czy kolumnowy?

W postaci diagramu można tę interpretację zilustrować w następujący sposób:

![img](./07_Zanurzenia_slow/bigram2.drawio.png "Diagram prostego bigramowego neuronowego modelu języka z wejściem w postaci one-hot")

